# Spotify Audio Features Dataset

Here we create a simple merged dataset of Spotify Audio Features. For more information, please check this repository on HuggingFace: [Spotify Audio Features](https://huggingface.co/datasets/ozefe/spotify_audio_features)

- https://annas-archive.org/torrents/spotify
- https://annas-archive.org/blog/backing-up-spotify.html

## Download Packages

In [ ]:
!apt-get install -y aria2 zstd

## Dependencies

In [ ]:
%pip install duckdb

In [ ]:
import sqlite3
import duckdb

from pathlib import Path

## Constants

In [ ]:
SPOTIFY_DATA_DOWNLOAD_MAIN_DIR = Path("./spotify")
SPOTIFY_DATA_DOWNLOAD_TORRENT_DIR = SPOTIFY_DATA_DOWNLOAD_MAIN_DIR / "annas_archive_spotify_2025_07_metadata"

SPOTIFY_TRACK_METADATA_ZST = SPOTIFY_DATA_DOWNLOAD_MAIN_DIR / "track_metadata.sqlite3.zst"
SPOTIFY_AUDIO_FEATURES_ZST = SPOTIFY_DATA_DOWNLOAD_MAIN_DIR / "audio_features.sqlite3.zst"

SPOTIFY_AUDIO_FEATURES_SQLITE3 = SPOTIFY_DATA_DOWNLOAD_MAIN_DIR / "audio_features.sqlite3"
SPOTIFY_TRACK_METADATA_SQLITE3 = SPOTIFY_DATA_DOWNLOAD_MAIN_DIR / "track_metadata.sqlite3"

SPOTIFY_MERGED_DATA_DIR = SPOTIFY_DATA_DOWNLOAD_MAIN_DIR / "merged_data"

In [ ]:
TORRENT_LINK = "https://annas-archive.org/dyn/small_file/torrents/other_aa/aa_misc_data/annas_archive_spotify_2025_07_metadata.torrent"

## Raw Data

### Download

In [ ]:
# Download ./annas_archive_spotify_2025_07_metadata/spotify_clean.sqlite3.zst
# and      ./annas_archive_spotify_2025_07_metadata/spotify_clean_audio_features.sqlite3.zst
!aria2c --check-integrity=true \
        --seed-time=0 \
        --bt-max-peers=0 \
        --select-file="4,5" \
        --bt-remove-unselected-file=true \
        --follow-torrent=mem \
        --remove-control-file=true \
        --bt-save-metadata=false \
        --rpc-save-upload-metadata=false \
        --dir {SPOTIFY_DATA_DOWNLOAD_MAIN_DIR} \
        {TORRENT_LINK}

# Move the file up one directory and change its name for better readability
!mv {SPOTIFY_DATA_DOWNLOAD_TORRENT_DIR}/spotify_clean.sqlite3.zst {SPOTIFY_TRACK_METADATA_ZST}
!mv {SPOTIFY_DATA_DOWNLOAD_TORRENT_DIR}/spotify_clean_audio_features.sqlite3.zst {SPOTIFY_AUDIO_FEATURES_ZST}

# Cleanup
!rm -f {SPOTIFY_DATA_DOWNLOAD_MAIN_DIR}/*.aria2
!rm -f {SPOTIFY_DATA_DOWNLOAD_MAIN_DIR}/*.torrent
!rm -rf {SPOTIFY_DATA_DOWNLOAD_TORRENT_DIR}

### Uncompress

In [ ]:
# Uncompress the ZStandard files to get SQLite3 database files (160GB)
!zstd --rm --decompress {SPOTIFY_TRACK_METADATA_ZST} -o {SPOTIFY_TRACK_METADATA_SQLITE3}
!zstd --rm --decompress {SPOTIFY_AUDIO_FEATURES_ZST} -o {SPOTIFY_AUDIO_FEATURES_SQLITE3}

## Merge and Convert to Parquet

In [ ]:
def merge_to_parquet():
    # Connect to an in-memory DuckDB instance
    con = duckdb.connect()

    # Install and load the SQLite extension so DuckDB can read our files directly
    con.execute("INSTALL sqlite; LOAD sqlite;")

    # This prevents the "Type Mismatch" crash by reading everything as raw text first.
    # We will fix the types in the SELECT statement below.
    con.execute("SET GLOBAL sqlite_all_varchar = true;")

    # Attach the two SQLite databases
    # This treats them like mounted drives; it does not load them into RAM.
    con.execute(f"ATTACH '{SPOTIFY_TRACK_METADATA_SQLITE3}' AS tm (TYPE SQLITE);")
    con.execute(f"ATTACH '{SPOTIFY_AUDIO_FEATURES_SQLITE3}' AS af (TYPE SQLITE);")

    # Define the query
    # We select rowid explicitly from both tables and alias them to avoid collision
    # We then CAST columns to their correct types. Since we read everything as VARCHAR,
    # we must cast them to BIGINT or DOUBLE.
    sql_query = """
    SELECT
        -- Track Metadata (Integers and Strings)
        tm.tracks.id,
        tm.tracks.name,
        TRY_CAST(tm.tracks.popularity AS BIGINT) AS popularity,

        -- Audio Features (Integers)
        TRY_CAST(af.track_audio_features.null_response AS BIGINT) AS null_response,
        TRY_CAST(af.track_audio_features.duration_ms AS BIGINT) AS duration_ms,
        TRY_CAST(af.track_audio_features.time_signature AS BIGINT) AS time_signature,
        TRY_CAST(af.track_audio_features.key AS BIGINT) AS key,
        TRY_CAST(af.track_audio_features.mode AS BIGINT) AS mode,

        -- Audio Features (Floats)
        -- We explicitly CAST these to DOUBLE to ensure the Parquet file uses Float types
        TRY_CAST(af.track_audio_features.tempo AS DOUBLE) AS tempo,
        TRY_CAST(af.track_audio_features.danceability AS DOUBLE) AS danceability,
        TRY_CAST(af.track_audio_features.energy AS DOUBLE) AS energy,
        TRY_CAST(af.track_audio_features.loudness AS DOUBLE) AS loudness,
        TRY_CAST(af.track_audio_features.speechiness AS DOUBLE) AS speechiness,
        TRY_CAST(af.track_audio_features.acousticness AS DOUBLE) AS acousticness,
        TRY_CAST(af.track_audio_features.instrumentalness AS DOUBLE) AS instrumentalness,
        TRY_CAST(af.track_audio_features.liveness AS DOUBLE) AS liveness,
        TRY_CAST(af.track_audio_features.valence AS DOUBLE) AS valence

    FROM tm.tracks
    JOIN af.track_audio_features
      ON tm.tracks.id = af.track_audio_features.track_id
    """

    print("Starting merge and write... this may take a while depending on disk speed.")

    # COPY ... TO ... is the fastest way to export.
    # We output to a folder ('merged_output').
    # PER_THREAD_OUTPUT=TRUE creates multiple files in parallel (much faster for 100GB).
    # ZSTD compression reduces file size significantly.
    con.sql(f"""
        COPY ({sql_query})
        TO '{SPOTIFY_MERGED_DATA_DIR}'
        (FORMAT PARQUET, PER_THREAD_OUTPUT TRUE, COMPRESSION 'ZSTD')
    """)

    print(f"Done! Data saved in '{SPOTIFY_MERGED_DATA_DIR}' folder.")

In [ ]:
merge_to_parquet()

## Metadata Information

### Audio Features

> Official API Documentation: https://developer.spotify.com/documentation/web-api/reference/get-audio-features

- **`track_id`**: The Spotify ID (Base62) for the track.
- **`null_response`**: true if the API returned null for the whole request
- **`duration_ms`**: The duration of the track in milliseconds.
- **`time_signature`**: An estimated time signature. The time signature (meter) is a notational convention to specify how many beats are in each bar (or measure). The time signature ranges from 3 to 7 indicating time signatures of "3/4" to "7/4".
- **`tempo`**: The overall estimated tempo of a track in beats per minute (BPM). In musical terminology, tempo is the speed or pace of a given piece and derives directly from the average beat duration.
- **`key`**: The key the track is in. Integers map to pitches using standard Pitch Class (https://en.wikipedia.org/wiki/Pitch_class) notation. E.g. 0 = C, 1 = C♯/D♭, 2 = D, and so on. If no key was detected, the value is -1.
- **`mode`**: Mode indicates the modality (major or minor) of a track, the type of scale from which its melodic content is derived. Major is represented by 1 and minor is 0.
- **`danceability`**: Danceability describes how suitable a track is for dancing based on a combination of musical elements including tempo, rhythm stability, beat strength, and overall regularity. A value of 0.0 is least danceable and 1.0 is most danceable.
- **`energy`**: Energy is a measure from 0.0 to 1.0 and represents a perceptual measure of intensity and activity. Typically, energetic tracks feel fast, loud, and noisy. For example, death metal has high energy, while a Bach prelude scores low on the scale. Perceptual features contributing to this attribute include dynamic range, perceived loudness, timbre, onset rate, and general entropy.
- **`loudness`**: The overall loudness of a track in decibels (dB). Loudness values are averaged across the entire track and are useful for comparing relative loudness of tracks. Loudness is the quality of a sound that is the primary psychological correlate of physical strength (amplitude). Values typically range between -60 and 0 db.
- **`speechiness`**: Speechiness detects the presence of spoken words in a track. The more exclusively speech-like the recording (e.g. talk show, audio book, poetry), the closer to 1.0 the attribute value. Values above 0.66 describe tracks that are probably made entirely of spoken words. Values between 0.33 and 0.66 describe tracks that may contain both music and speech, either in sections or layered, including such cases as rap music. Values below 0.33 most likely represent music and other non-speech-like tracks.
- **`acousticness`**: A confidence measure from 0.0 to 1.0 of whether the track is acoustic. 1.0 represents high confidence the track is acoustic.
- **`instrumentalness`**: Predicts whether a track contains no vocals. "Ooh" and "aah" sounds are treated as instrumental in this context. Rap or spoken word tracks are clearly "vocal". The closer the instrumentalness value is to 1.0, the greater likelihood the track contains no vocal content. Values above 0.5 are intended to represent instrumental tracks, but confidence is higher as the value approaches 1.0.
- **`liveness`**: Detects the presence of an audience in the recording. Higher liveness values represent an increased probability that the track was performed live. A value above 0.8 provides strong likelihood that the track is live.
- **`valence`**: A measure from 0.0 to 1.0 describing the musical positiveness conveyed by a track. Tracks with high valence sound more positive (e.g. happy, cheerful, euphoric), while tracks with low valence sound more negative (e.g. sad, depressed, angry).

### Track Metadata

> Official API Documentation: https://developer.spotify.com/documentation/web-api/reference/get-track

- **`id`**: The Spotify ID (Base62) for the track.
- **`name`**: The name of the track.
- **`popularity`**: The popularity of the track. The value will be between 0 and 100, with 100 being the most popular. The popularity of a track is a value between 0 and 100, with 100 being the most popular. The popularity is calculated by algorithm and is based, in the most part, on the total number of plays the track has had and how recent those plays are. Generally speaking, songs that are being played a lot now will have a higher popularity than songs that were played a lot in the past. Duplicate tracks (e.g. the same track from a single and an album) are rated independently. Artist and album popularity is derived mathematically from track popularity. **Note**: *the popularity value may lag actual popularity by a few days: the value is not updated in real time.*